# Cours 4 : Machine Learning - Algorithmes supervisés (2/2)

## Préambule

Les objectifs de cette séance (3h) sont :
* Préparation des bases de modélisation (sampling)
* Construire un modèle de Machine Learning (cross-validation et hyperparamétrage) pour résoudre un problème de classification
* Analyser les performances du modèle

## Préparation du workspace

### Import de librairies 

In [ ]:
# Données
import numpy as np
import pandas as pd

# Graphiques
import seaborn as sns

sns.set()
import plotly.express as px

# Machine Learning
import sklearn.preprocessing as preproc
from imblearn.over_sampling import RandomOverSampler

# Statistiques
from scipy.stats import chi2_contingency
from sklearn import metrics
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import (
  GridSearchCV,
  KFold,
  StratifiedKFold,
  cross_val_score,
  train_test_split,
)


### Définition des fonctions 

In [104]:
def cramers_V(var1,var2) :
  crosstab = np.array(pd.crosstab(var1,var2, rownames=None, colnames=None)) # Cross table building
  stat = chi2_contingency(crosstab)[0] # Keeping of the test statistic of the Chi2 test
  obs = np.sum(crosstab) # Number of observations
  mini = min(crosstab.shape)-1 # Take the minimum value between the columns and the rows of the cross table
  return (stat/(obs*mini))

### Constantes

In [105]:
input_path = "./1_inputs"
output_path = "./2_outputs"

### Import des données

In [106]:
path = input_path + '/base_retraitee.csv'
data_retraitee = pd.read_csv(path, sep=",", decimal=".")

## Préparation de la base de données

Dans cette partie nous souhaitons expliquer la survenance d'un sinistre en fonction des variables explicatives i.e. une variable binaire qui : 
* est égale à 1 si la personne a eu 1 ou plus de sinistres.
* est égale à 0 le cas échéant.

In [107]:
# Calculez la variable "sinistré" qui est 1 si la personne a eu un ou plusieurs sinistres, 0 sinon
data_retraitee["sinistré"] = data_retraitee["NB"] > 0
data_retraitee["sinistré"] = data_retraitee["sinistré"].astype(int)
data_retraitee

ANNEE_CTR CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION  \
0           2019             (-1,0]                        ANNUEL   
1           2019             (-1,0]                        ANNUEL   
2           2021              (1,2]                        ANNUEL   
3           2021              (2,5]                        ANNUEL   
4           2018              (2,5]                       MENSUEL   
...          ...                ...                           ...   
14231       2021              (2,5]                       MENSUEL   
14232       2019              (2,5]                       MENSUEL   
14233       2017             (-1,0]                        ANNUEL   
14234       2018             (-1,0]                   TRIMESTRIEL   
14235       2017             (-1,0]                        ANNUEL   

           GROUPE_KM ZONE_RISQUE  AGE_ASSURE_PRINCIPAL GENRE  \
0      [20000;40000[           B                    54     M   
1      [20000;40000[           B                    88     F   
2          [0;20000[           D                    35     F   
3          [0;20000[           C                    46     M   
4      [20000;40000[           A                    46     F   
...              ...         ...                   ...   ...   
14231      [0;20000[           D                    55     M   
14232  [20000;40000[           A                    33     M   
14233      [0;20000[           A                    62     M   
14234  [20000;40000[           D                    20     M   
14235      [0;20000[           C                    73     F   

       DEUXIEME_CONDUCTEUR  ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  ENERGIE  \
0                    False                 47              2016.0  ESSENCE   
1                     True                 55              2018.0   DIESEL   
2                     True                 16              2017.0  ESSENCE   
3                    False                 44              2018.0  ESSENCE   
4                    False                 31              2009.0   DIESEL   
...                    ...                ...                 ...      ...   
14231                False                 49              2017.0  ESSENCE   
14232                False                 14              2017.0  ESSENCE   
14233                False                 58              2017.0  ESSENCE   
14234                False                  7              2016.0   DIESEL   
14235                False                 41              2017.0  ESSENCE   

      EQUIPEMENT_SECURITE VALEUR_DU_BIEN  NB  CHARGE        EXPO  sinistré  
0                    FAUX  [10000;15000[   0     0.0  245.327869         0  
1                    VRAI  [20000;25000[   0     0.0  230.368852         0  
2                    FAUX  [15000;20000[   0     0.0  300.000000         0  
3                    VRAI  [35000;99999[   0     0.0  304.000000         0  
4                    FAUX  [10000;15000[   0     0.0  365.000000         0  
...                   ...            ...  ..     ...         ...       ...  
14231                FAUX  [20000;25000[   0     0.0  181.000000         0  
14232                FAUX  [10000;15000[   0     0.0  364.669399         0  
14233                VRAI  [10000;15000[   0     0.0  182.000000         0  
14234                FAUX  [25000;35000[   0     0.0    9.000000         0  
14235                FAUX  [10000;15000[   0     0.0   52.000000         0  

[14236 rows x 17 columns]

**Exercice :** construisez les statistiques descriptives de la base utilisée. Notamment la distribution de la variable réponse.

In [108]:
# Observation de la distribution
fig = px.histogram(data_retraitee, x="sinistré", title="Distribution de la variable 'sinistré'")
fig.show()

#### Etude des corrélations parmi les variables explicatives

In [109]:
data_set = data_retraitee.drop("sinistré", axis=1)
data_set.shape

(14236, 16)

In [110]:
# Séparation en variables qualitatives ou catégorielles
variables_na = []
variables_numeriques = []
variables_01 = []
variables_categorielles = []
for colu in data_set.columns:
    if True in data_set[colu].isna().unique():
        variables_na.append(data_set[colu])
    else:
        if str(data_set[colu].dtypes) in ["int32", "int64", "float64"]:
            if len(data_set[colu].unique()) == 2:
                variables_categorielles.append(data_set[colu])
            else:
                variables_numeriques.append(data_set[colu])
        else:
            if len(data_set[colu].unique()) == 2:
                variables_categorielles.append(data_set[colu])
            else:
                variables_categorielles.append(data_set[colu])


##### Corrélation des variables catégorielles :

In [111]:
vars_categorielles = pd.DataFrame(variables_categorielles).transpose()

In [112]:
# Test du V de Cramer
rows = []

for var1 in vars_categorielles:
    col = []
    for var2 in vars_categorielles:
        cramers = cramers_V(
            vars_categorielles[var1], vars_categorielles[var2]
        )  # V de Cramer
        col.append(round(cramers, 2))  # arrondi du résultat
    rows.append(col)

cramers_results = np.array(rows)
v_cramer_resultats = pd.DataFrame(
    cramers_results,
    columns=vars_categorielles.columns,
    index=vars_categorielles.columns,
)

v_cramer_resultats


CONTRAT_ANCIENNETE  \
CONTRAT_ANCIENNETE                           1.00   
FREQUENCE_PAIEMENT_COTISATION                0.00   
GROUPE_KM                                    0.01   
ZONE_RISQUE                                  0.02   
GENRE                                        0.00   
DEUXIEME_CONDUCTEUR                          0.00   
ENERGIE                                      0.00   
EQUIPEMENT_SECURITE                          0.01   
VALEUR_DU_BIEN                               0.00   

                               FREQUENCE_PAIEMENT_COTISATION  GROUPE_KM  \
CONTRAT_ANCIENNETE                                      0.00       0.01   
FREQUENCE_PAIEMENT_COTISATION                           1.00       0.00   
GROUPE_KM                                               0.00       1.00   
ZONE_RISQUE                                             0.00       0.01   
GENRE                                                   0.01       0.01   
DEUXIEME_CONDUCTEUR                                     0.00       0.00   
ENERGIE                                                 0.00       0.04   
EQUIPEMENT_SECURITE                                     0.01       0.01   
VALEUR_DU_BIEN                                          0.02       0.02   

                               ZONE_RISQUE  GENRE  DEUXIEME_CONDUCTEUR  \
CONTRAT_ANCIENNETE                    0.02   0.00                  0.0   
FREQUENCE_PAIEMENT_COTISATION         0.00   0.01                  0.0   
GROUPE_KM                             0.01   0.01                  0.0   
ZONE_RISQUE                           1.00   0.00                  0.0   
GENRE                                 0.00   1.00                  0.0   
DEUXIEME_CONDUCTEUR                   0.00   0.00                  1.0   
ENERGIE                               0.01   0.02                  0.0   
EQUIPEMENT_SECURITE                   0.03   0.01                  0.0   
VALEUR_DU_BIEN                        0.00   0.07                  0.0   

                               ENERGIE  EQUIPEMENT_SECURITE  VALEUR_DU_BIEN  
CONTRAT_ANCIENNETE                0.00                 0.01            0.00  
FREQUENCE_PAIEMENT_COTISATION     0.00                 0.01            0.02  
GROUPE_KM                         0.04                 0.01            0.02  
ZONE_RISQUE                       0.01                 0.03            0.00  
GENRE                             0.02                 0.01            0.07  
DEUXIEME_CONDUCTEUR               0.00                 0.00            0.00  
ENERGIE                           1.00                 0.02            0.08  
EQUIPEMENT_SECURITE               0.02                 1.00            0.07  
VALEUR_DU_BIEN                    0.08                 0.07            1.00

In [113]:
# On repère les variables trop corrélées
for i in range(v_cramer_resultats.shape[0]):
    for j in range(i + 1, v_cramer_resultats.shape[0]):
        if v_cramer_resultats.iloc[i, j] > 0.7:
            print(
                v_cramer_resultats.index.to_numpy()[i]
                + " et "
                + v_cramer_resultats.columns[j]
                + " sont trop dépendantes, V-CRAMER = "
                + str(v_cramer_resultats.iloc[i, j])
            )


##### Corrélation des variables numériques :

In [114]:
vars_numeriques = pd.DataFrame(variables_numeriques).transpose()

**Question :** quels sont vos commentaires ?

In [115]:
# Corrélation de Pearson
correlations_num = vars_numeriques.corr(method="pearson")
correlations_num

ANNEE_CTR  AGE_ASSURE_PRINCIPAL  ANCIENNETE_PERMIS  \
ANNEE_CTR              1.000000              0.048023           0.043983   
AGE_ASSURE_PRINCIPAL   0.048023              1.000000           0.498743   
ANCIENNETE_PERMIS      0.043983              0.498743           1.000000   
ANNEE_CONSTRUCTION     0.361550             -0.059184          -0.029814   
NB                    -0.057752             -0.012425          -0.008704   
CHARGE                -0.028901             -0.020908          -0.011347   
EXPO                  -0.047705              0.060963           0.032461   

                      ANNEE_CONSTRUCTION        NB    CHARGE      EXPO  
ANNEE_CTR                       0.361550 -0.057752 -0.028901 -0.047705  
AGE_ASSURE_PRINCIPAL           -0.059184 -0.012425 -0.020908  0.060963  
ANCIENNETE_PERMIS              -0.029814 -0.008704 -0.011347  0.032461  
ANNEE_CONSTRUCTION              1.000000 -0.014377 -0.001230 -0.073953  
NB                             -0.014377  1.000000  0.507107  0.050702  
CHARGE                         -0.001230  0.507107  1.000000 -0.021419  
EXPO                           -0.073953  0.050702 -0.021419  1.000000

In [116]:
# On repère les variables trop corrélées
nb_variables = correlations_num.shape[0]
for i in range(nb_variables):
    for j in range(i + 1, nb_variables):
        if abs(correlations_num.iloc[i, j]) > 0.7:
            print(
                correlations_num.index.to_numpy()[i]
                + " et "
                + correlations_num.columns[j]
                + " sont trop dépendantes, corr = "
                + str(correlations_num.iloc[i, j])
            )

#### Preprocessing

Deux étapes sont nécessaires avant de lancer l'apprentissage d'un modèle, c'est ce qu'on connait comme le *Preprocessing* :

* Les modèles proposés par la librairie "sklearn" ne gèrent que des variables numériques. Il est donc nécessaire de transformer les variables catégorielles en variables numériques : ce processus s'appelle le *One Hot Encoding*.
* Normaliser les données numériques

**Exercice :** proposez un bout de code permettant de réaliser le One Hot Encoding des variables catégorielles. Vous pourrez utiliser la fonction "preproc.OneHotEncoder" de la librairie sklearn

In [117]:
# One hot encoding des variables catégorielles
preproc_ohe = preproc.OneHotEncoder(handle_unknown="ignore")
preproc_ohe = preproc.OneHotEncoder(drop="first", sparse_output=False).fit(
    vars_categorielles
)

variables_categorielles_ohe = preproc_ohe.transform(vars_categorielles)
variables_categorielles_ohe = pd.DataFrame(
    variables_categorielles_ohe,
    columns=preproc_ohe.get_feature_names_out(vars_categorielles.columns),
)
variables_categorielles_ohe.head()

CONTRAT_ANCIENNETE_(0,1]  CONTRAT_ANCIENNETE_(1,2]  \
0                       0.0                       0.0   
1                       0.0                       0.0   
2                       0.0                       1.0   
3                       0.0                       0.0   
4                       0.0                       0.0   

   CONTRAT_ANCIENNETE_(2,5]  CONTRAT_ANCIENNETE_(5,10]  \
0                       0.0                        0.0   
1                       0.0                        0.0   
2                       0.0                        0.0   
3                       1.0                        0.0   
4                       1.0                        0.0   

   FREQUENCE_PAIEMENT_COTISATION_MENSUEL  \
0                                    0.0   
1                                    0.0   
2                                    0.0   
3                                    0.0   
4                                    1.0   

   FREQUENCE_PAIEMENT_COTISATION_TRIMESTRIEL  GROUPE_KM_[20000;40000[  \
0                                        0.0                      1.0   
1                                        0.0                      1.0   
2                                        0.0                      0.0   
3                                        0.0                      0.0   
4                                        0.0                      1.0   

   GROUPE_KM_[40000;60000[  GROUPE_KM_[60000;99999[  ZONE_RISQUE_B  ...  \
0                      0.0                      0.0            1.0  ...   
1                      0.0                      0.0            1.0  ...   
2                      0.0                      0.0            0.0  ...   
3                      0.0                      0.0            0.0  ...   
4                      0.0                      0.0            0.0  ...   

   GENRE_M  DEUXIEME_CONDUCTEUR_True  ENERGIE_DIESEL  ENERGIE_ESSENCE  \
0      1.0                       0.0             0.0              1.0   
1      0.0                       1.0             1.0              0.0   
2      0.0                       1.0             0.0              1.0   
3      1.0                       0.0             0.0              1.0   
4      0.0                       0.0             1.0              0.0   

   EQUIPEMENT_SECURITE_VRAI  VALEUR_DU_BIEN_[10000;15000[  \
0                       0.0                           1.0   
1                       1.0                           0.0   
2                       0.0                           0.0   
3                       1.0                           0.0   
4                       0.0                           1.0   

   VALEUR_DU_BIEN_[15000;20000[  VALEUR_DU_BIEN_[20000;25000[  \
0                           0.0                           0.0   
1                           0.0                           1.0   
2                           1.0                           0.0   
3                           0.0                           0.0   
4                           0.0                           0.0   

   VALEUR_DU_BIEN_[25000;35000[  VALEUR_DU_BIEN_[35000;99999[  
0                           0.0                           0.0  
1                           0.0                           0.0  
2                           0.0                           0.0  
3                           0.0                           1.0  
4                           0.0                           0.0  

[5 rows x 35 columns]

**Exercice :** proposez un bout de code permettant noramliser les variables numériques présentes dans la base. Vous pourrez utiliser la fonction "preproc.StandardScaler" de la librairie sklearn

In [118]:
# Normalisation des varibales numériques
preproc_scale = preproc.StandardScaler(with_mean=True, with_std=True)
preproc_scale.fit(vars_numeriques)

vars_numeriques_scaled = preproc_scale.transform(vars_numeriques)
vars_numeriques_scaled = pd.DataFrame(
    vars_numeriques_scaled, columns=vars_numeriques.columns
)
vars_numeriques_scaled.head()

ANNEE_CTR  AGE_ASSURE_PRINCIPAL  ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  \
0   0.139356              0.658287           0.563588            0.174011   
1   0.139356              3.151628           0.987434            0.744207   
2   1.347192             -0.735051          -1.078814            0.459109   
3   1.347192              0.071618           0.404646            0.744207   
4  -0.464562              0.071618          -0.284103           -1.821676   

         NB    CHARGE      EXPO  
0 -0.242029 -0.181254 -0.289146  
1 -0.242029 -0.181254 -0.427093  
2 -0.242029 -0.181254  0.215021  
3 -0.242029 -0.181254  0.251907  
4 -0.242029 -0.181254  0.814427

## Algorithme supervisé : Gradient Boosting

A ce stade, nous avons vu les différentes étapes pour lancer un algorithme de Machine Learning. Néanmoins, ces étapes ne sont pas suffisantes pour construire un modèle performant.  
En effet, afin de construire un modèle performant le Data Scientist doit agir sur l'apprentissage du modèle. Dans ce qui suit nous :
* Changerons d'algorithme pour utiliser un algorithme plus performant (Gradient Boosting)
* Raliserons un *grid search* sur les paramètres du modèle
* Appliquerons l'apprentissage par validation croisée


**Exercice :** Implémentez l'algorithme du Gradient Boosting en appliquant les techniques vues lors des derniers cours (sampling, Grid search et Cross Validation)  
**Remarques :**
* Vous pouvez utiliser les modèles "GradientBoostingClassifier" et "GridSearchCV" de la libraire Sklearn.  
* Pensez à utiliser les métriques relatives aux problèmes de classification.

#### Sampling

In [119]:
X_global = vars_numeriques_scaled.merge(
    variables_categorielles_ohe, left_index=True, right_index=True
)

# Réorganisation des données
X = X_global.to_numpy()
Y = data_retraitee["sinistré"]

# Sampling en 80% train et 20% test
X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.2, random_state=42, stratify=Y
)

#### Fitting avec Cross-Validation et *Grid Search*

In [120]:
# Définir la grille d'hyperparamètres à rechercher
param_grid = {
    "n_estimators": [100, 200, 250],
    "learning_rate": [0.5, 0.7, 0.9],
}
scoring = 'recall'
# Nombre de folds pour la validation croisée
num_folds = 5

In [121]:
# Initialisation du modèle GradientBoostingClassifier
gbc = GradientBoostingClassifier(random_state=42)

# Création de l'objet GridSearchCV pour la recherche sur grille avec validation croisée
grid_search = GridSearchCV(
    estimator=gbc,
    param_grid=param_grid,
    cv=StratifiedKFold(
        n_splits=num_folds, shuffle=True, random_state=42
    ),  # Validation croisée avec 5 folds
    scoring=scoring,  # Métrique d'évaluation (moins c'est mieux)
    n_jobs=-1,  # Utiliser tous les cœurs du processeur
)

# Exécution de la recherche sur grille
grid_search.fit(X_train, y_train)

# Afficher les meilleurs hyperparamètres
best_params = grid_search.best_params_
print("Meilleurs hyperparamètres : ", best_params)


Meilleurs hyperparamètres :  {'learning_rate': 0.5, 'n_estimators': 100}


In [122]:
# Initialiser le modèle final avec les meilleurs hyperparamètres
best_gbc = GradientBoostingClassifier(random_state=42, **best_params)

In [123]:
# Cross validation
# RMSE de chaque fold
rmse_scores = cross_val_score(best_gbc, X_train, y_train, cv=num_folds, scoring=scoring)

# Afficher les scores pour chaque fold
for i, score in enumerate(rmse_scores):
    print(f"RMSE pour le fold {i + 1}: {score}")

# MSE de chaque fold
mse_scores = cross_val_score(best_gbc, X_train, y_train, cv=num_folds, scoring=scoring)

# Afficher les scores pour chaque fold
print("\n")
for i, score in enumerate(mse_scores):
    print(f"MSE pour le fold {i + 1}: {score}")

# MAE de chaque fold
mae_scores = cross_val_score(best_gbc, X_train, y_train, cv=num_folds, scoring=scoring)

# Afficher les scores pour chaque fold
print("\n")
for i, score in enumerate(mae_scores):
    print(f"MAE pour le fold {i + 1}: {score}")


RMSE pour le fold 1: 1.0
RMSE pour le fold 2: 1.0
RMSE pour le fold 3: 1.0
RMSE pour le fold 4: 1.0
RMSE pour le fold 5: 1.0


MSE pour le fold 1: 1.0
MSE pour le fold 2: 1.0
MSE pour le fold 3: 1.0
MSE pour le fold 4: 1.0
MSE pour le fold 5: 1.0


MAE pour le fold 1: 1.0
MAE pour le fold 2: 1.0
MAE pour le fold 3: 1.0
MAE pour le fold 4: 1.0
MAE pour le fold 5: 1.0


#### Validation du modèle -  métriques

**Exercice :** 
* Construisez la matrice de confusion (metrics.confusion_matrix).
* Calculez les métriques : accuracy, recall & precision.